In [2]:
import requests, uuid

# Add your key and endpoint
with open("bing.key", "r") as key_file:
    key = key_file.read()
endpoint = "https://api.cognitive.microsofttranslator.com"

# location, also known as region.
# required if you're using a multi-service or regional (not global) resource. It can be found in the Azure portal on the Keys and Endpoint page.
location = "eastus"

path = '/translate'
constructed_url = endpoint + path

params = {
    'api-version': '3.0',
    'from': 'yue',
    'to': ['zh-Hant']
}

headers = {
    'Ocp-Apim-Subscription-Key': key,
    # location required if you're using a multi-service or regional (not global) resource.
    'Ocp-Apim-Subscription-Region': location,
    'Content-type': 'application/json',
    'X-ClientTraceId': str(uuid.uuid4())
}

# https://stackoverflow.com/a/312464/6798201
def chunks(lst, n):
    """Yield successive n-sized chunks from lst."""
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

In [5]:
"""
Translate test sentences
"""

# You can pass more than one object in body.
with open("../para/test/test.typos.can", "r") as input_file:
    body = [{'text': line} for line in input_file.read().splitlines()]

# Clear previous outputs
open("../test.typos.pred.bing.man", 'w').close()

# Split translation request into chunks of 500 lines (10,000 character limit per request)
with open("../test.typos.pred.bing.man", "a+") as output_file:
    for chunk in chunks(body, 500):
        request = requests.post(constructed_url, params=params, headers=headers, json=chunk)
        response = request.json()
        for line in response:
            output_file.write(line['translations'][0]['text'] + "\n")

KeyboardInterrupt: 

In [17]:
"""
Translate training sentences
"""

# You can pass more than one object in body.
with open("bing.can", "r") as input_file:
    body = [{'text': line} for line in input_file.read().splitlines()]

# Clear previous outputs
open("bing.man", 'w').close()

from tqdm import tqdm
import time

# Split translation request into chunks of 400 lines (10,000 character limit per request)
with open("bing.man", "a+") as output_file:
    for chunk in tqdm(list(chunks(body, 400))):
        request = requests.post(constructed_url, params=params, headers=headers, json=chunk)
        response = request.json()
        for line in response:
            output_file.write(line['translations'][0]['text'] + "\n")
        # Slow down because of hourly request limit for free tier
        time.sleep(5)


  0%|          | 0/110 [00:01<?, ?it/s]


KeyboardInterrupt: 

In [18]:
# You can pass more than one object in body.
with open("../train/abc.can", "r") as input_file:
    body = [{'text': line} for line in input_file.read().splitlines() if len(line) >= 5]

from tqdm import tqdm
import time

# Split translation request into chunks of 400 lines (10,000 character limit per request)
with open("bing.man", "a+") as output_file:
    for chunk in tqdm(list(chunks(body, 400))):
        request = requests.post(constructed_url, params=params, headers=headers, json=chunk)
        response = request.json()
        for line in response:
            output_file.write(line['translations'][0]['text'] + "\n")
        # Slow down because of hourly request limit for free tier
        time.sleep(5)

100%|██████████| 38/38 [03:33<00:00,  5.61s/it]


In [3]:
# You can pass more than one object in body.
with open("../train/lihkg.filtered.can", "r") as input_file:
    body = [{'text': line} for line in input_file.read().splitlines()]

from tqdm import tqdm
import time

# Split translation request into chunks of 400 lines (10,000 character limit per request)
with open("lihkg.filtered.man", "w+") as output_file:
    for chunk in tqdm(list(chunks(body, 400))):
        request = requests.post(constructed_url, params=params, headers=headers, json=chunk)
        response = request.json()
        for line in response:
            output_file.write(line['translations'][0]['text'] + "\n")
        # Slow down because of hourly request limit for free tier
        time.sleep(3)

100%|██████████| 352/352 [21:28<00:00,  3.66s/it]
